In [ ]:
#This is the exercise on how to obtain the Regge-Wheeler equation in Schwarzschild black hole 
#Starting from massless scalar field equation D_m D^m Φ = 0 

In [1]:
#Set the display into latex form 
%display latex
#Parallel computations
#Parallelism().set(nproc=8)
#Define a 4d manifold with Lorentzian signature
M = Manifold(4, 'M', structure='Lorentzian')
#Define a coordinate X  = (t,r,theta,phi) with specific charts
X.<t,r,th,ph> = M.chart(r"t r:(0,+oo) th:(0,pi):\theta ph:(0,2*pi):\phi")
#Define mass parameter 
f=function('f')
#Define metric
g=M.metric()
g[0,0] = -f(r)
g[1,1] = 1/f(r)
g[2,2] = r^2
g[3,3] = (r*sin(th))^2
#Print out the metric
g.display()

g = -f(r) dt⊗dt + 1/f(r) dr⊗dr + r^2 dth⊗dth + r^2*sin(th)^2 dph⊗dph

In [2]:
#Define functiosn in the scalar fields 
w=var('ω')
Y=function('Y')
R=function('R')
Ph=function('Ph')

In [3]:
#Define covariant derivative through connection
nab = g.connection(name='nabla', latex_name=r'\nabla')

In [4]:
#Define scalar field in SageManifold to enable covariant derivative stuff
Ph_s = M.scalar_field(Ph(t,r,th,ph), latex_name=r'\Phi')
#For some unknown reason the Laplacian operator works here...unlike the case of the sphere (maybe you can figure this out!)
laplPh = Ph_s.laplacian()
#Expression for d^2ph --multiply common factor to make things looks nicer
ddPh = laplPh.expr()*(r^2*f(r)*sin(th)^2)


In [5]:
#Let's print out ddPhi just to see how ugly this is 
ddPh

cos(th)*f(r)*sin(th)*diff(Ph(t, r, th, ph), th) + (r^2*f(r)^2*diff(Ph(t, r, th, ph), r, r) - r^2*diff(Ph(t, r, th, ph), t, t) + (r^2*f(r)*diff(f(r), r) + 2*r*f(r)^2)*diff(Ph(t, r, th, ph), r) + f(r)*diff(Ph(t, r, th, ph), th, th))*sin(th)^2 + f(r)*diff(Ph(t, r, th, ph), ph, ph)

In [6]:
# laplPh in itself is a map. This is why we need to act on it with .expr()
laplPh.display()

M → ℝ
(t, r, th, ph) ↦ (cos(th)*f(r)*sin(th)*d(Ph)/dth + (r^2*f(r)^2*d^2(Ph)/dr^2 - r^2*d^2(Ph)/dt^2 + (r^2*f(r)*d(f)/dr + 2*r*f(r)^2)*d(Ph)/dr + f(r)*d^2(Ph)/dth^2)*sin(th)^2 + f(r)*d^2(Ph)/dph^2)/(r^2*f(r)*sin(th)^2)

In [7]:
#Define a substitute function Ph = exp(-I*w*t)*R(r)/r*Y(th,ph)
PhSubs(t,r,th,ph) = exp(-I*w*t)*R(r)/r*Y(th,ph)

In [8]:
#Substitute the above ansatz to equation of motion for Ph
ddPh1=ddPh.substitute_function(Ph,PhSubs).factor().simplify()
ddPh1

(r^2*ω^2*R(r)*Y(th, ph)*sin(th)^2 + r^2*Y(th, ph)*f(r)^2*sin(th)^2*diff(R(r), r, r) + r^2*Y(th, ph)*f(r)*sin(th)^2*diff(R(r), r)*diff(f(r), r) - r*R(r)*Y(th, ph)*f(r)*sin(th)^2*diff(f(r), r) + R(r)*cos(th)*f(r)*sin(th)*diff(Y(th, ph), th) + R(r)*f(r)*sin(th)^2*diff(Y(th, ph), th, th) + R(r)*f(r)*diff(Y(th, ph), ph, ph))*e^(-I*t*ω)/r

In [10]:
#Define variable l
var('l')
#Substitute spherical harmonic property (see wikipedia )
YsphProp=1/sin(th)*diff(diff(Y(th,ph),th)*sin(th),th) + 1/sin(th)^2*diff(Y(th,ph),ph,ph)-l*(l+1)*Y(th,ph)
#Solve for YsphProp ==0 to expression d^2Y/dϕ^2 by other things 
subddY = solve(YsphProp==0,diff(Y(th,ph),ph,ph))
#Let's print it out to see that Sage does what we asked
subddY

[diff(Y(th, ph), ph, ph) == (l^2 + l)*Y(th, ph)*sin(th)^2 - cos(th)*sin(th)*diff(Y(th, ph), th) - sin(th)^2*diff(Y(th, ph), th, th)]

In [11]:
#์Now let's substitute the definition of Ph. Since e^{-I w t} factor out, we can set t==0
ddPhsub2=ddPh1.substitute(subddY).subs(t==0).expand()
ddPhsub2

r*ω^2*R(r)*Y(th, ph)*sin(th)^2 + r*Y(th, ph)*f(r)^2*sin(th)^2*diff(R(r), r, r) + r*Y(th, ph)*f(r)*sin(th)^2*diff(R(r), r)*diff(f(r), r) + l^2*R(r)*Y(th, ph)*f(r)*sin(th)^2/r - R(r)*Y(th, ph)*f(r)*sin(th)^2*diff(f(r), r) + l*R(r)*Y(th, ph)*f(r)*sin(th)^2/r

In [12]:
#factorised Y sin^2(th) and try to simplify. Somehow Sage doesn't do it for us
ddPhsub3 = ddPhsub2/(Y(th,ph)*sin(th)^2).expand()
ddPhsub3

(r*ω^2*R(r)*Y(th, ph)*sin(th)^2 + r*Y(th, ph)*f(r)^2*sin(th)^2*diff(R(r), r, r) + r*Y(th, ph)*f(r)*sin(th)^2*diff(R(r), r)*diff(f(r), r) + l^2*R(r)*Y(th, ph)*f(r)*sin(th)^2/r - R(r)*Y(th, ph)*f(r)*sin(th)^2*diff(f(r), r) + l*R(r)*Y(th, ph)*f(r)*sin(th)^2/r)/(Y(th, ph)*sin(th)^2)

In [13]:
#Apparently Sage is not smart enough to simplify this 
#but we can look at each coefficients 
#Coefficient of R
coR = ddPhsub3.coefficient(R(r)).full_simplify()
#Coefficient of dR/dr
codR=ddPhsub3.coefficient(diff(R(r),r)).full_simplify()
#Coefficient of d^2R/dr^2
coddR=ddPhsub3.coefficient(diff(R(r),r,r)).full_simplify()
#Recombine them together and print it out
ddPhsub4=coR*R(r)+codR*diff(R(r),r)+coddR*diff(R(r),r,r)
ddPhsub4

r*f(r)^2*diff(R(r), r, r) + r*f(r)*diff(R(r), r)*diff(f(r), r) + (r^2*ω^2 - r*f(r)*diff(f(r), r) + (l^2 + l)*f(r))*R(r)/r

In [14]:
#Now, let's define r* as a function of r
rstar = function('r^*')(r)
#See what dR(r*)/dr = (dR(r*)/dr*)(dr*/dr) looks like. Knowing that dr*/dr = 1/f(r) from definition of tortoise coordinate
dRdr=diff(R(rstar),r).subs(diff(rstar,r)==1/f(r))
dRdr

D[0](R)(r^*(r))/f(r)

In [15]:
#At this stage we can do the manipulation by hand
#or perform the following substitution
#This is how to write d^2R(r*)/dr^2 
d2Rdr2= diff(diff(R(rstar),r).subs(diff(rstar,r)==1/f(r)),r).subs(diff(rstar,r)==1/f(r))
#Note dR/dr* and d^2R/dr*^2
dRdrStar = diff(R(rstar))/diff(rstar,r)
dRdr2Star=diff(dRdrStar)/diff(rstar,r)
#This is what these dR/dr* and d^2R/dr*^2 looks like
dRdr,d2Rdr2

(D[0](R)(r^*(r))/f(r),
 -D[0](R)(r^*(r))*diff(f(r), r)/f(r)^2 + D[0, 0](R)(r^*(r))/f(r)^2)

In [16]:
#Now make a substitution to replace dR/dr into dR/dr* and d^2R/dr^2 into d^2R/dr*^2
eomRstar = 1/r*ddPhsub4.subs(diff(R(r),r)==dRdr).subs(diff(R(r),r,r)==d2Rdr2).expand()
eomRstar.collect(R(r))

(ω^2 + l^2*f(r)/r^2 - f(r)*diff(f(r), r)/r + l*f(r)/r^2)*R(r) + D[0, 0](R)(r^*(r))

In [17]:
#Maybe collect the potential term (coefficient of R(r)) more nicely
eomRstar.coefficient(R(r)).expand().full_simplify()

(r^2*ω^2 - r*f(r)*diff(f(r), r) + (l^2 + l)*f(r))/r^2